In [1]:
from configuracoes_notebooks import set_proj_dir
set_proj_dir()

O diretorio do seu projeto é coleta_cebrap
Caminho absoluto do diretorio encontrado C:\Users\x526378\Desktop\projetos\cebrap\coleta_cebrap
Caminho no path.


In [2]:
import os
import geopandas as gpd

from notebooks.jupyter import utils
from utils import (
    get_data_diretorio,
    save_parquet_excel,
)

# Overlay Intersection entre área de Cobertura Vegetal e Distritos

In [3]:
data_path = get_data_diretorio()

# Dependências

Este notebook é dependente dos assets resultantes dos notebooks ../../arborizacao_viaria/carregar_dados/malha_distritos e load_data/malha_cobertura_vegetal

In [4]:
cobveg_path = os.path.join(
    data_path, 
    'assets', 
    'malha_cobertura_vegetal.parquet'
)
gdf_cobveg = gpd.read_parquet(cobveg_path)

In [5]:
distritos_path = os.path.join(data_path, 'assets', 'distrito_ibge.parquet')
gdf_distritos = gpd.read_parquet(distritos_path)

# Orvelay cobertura vegetal por Distrito

In [6]:
gdf_cobveg.sample(2)

cd_cob_veg  cd_identi0  cd_categor  cd_subcate  cd_subcat0  \
220964    220965.0    221817.0        14.0         0.0         0.0   
23734      23735.0     23843.0        13.0         0.0         0.0   

        qt_altura_                                           geometry  
220964         0.0  POLYGON ((330298.742 7374487.027, 330299.87 73...  
23734          0.0  POLYGON ((331833.336 7394733.893, 331833.552 7...

Como podemos ver na coluna de geometria, as áreas de cobertura vegetal são polígonos. Para calcular corretamente a quantidade de área verde por distritos, precisamos usar uma função chamada 'overlay intersection'.

Iniciamos registrado valor de cada polígono ANTES do processo de recorte com o overlay.

In [7]:
gdf_cobveg['area_cob_veg']=gdf_cobveg['geometry'].area

Agora utilizaremos a função do overlay:

In [8]:
overlay_gdf = gpd.overlay(
    gdf_cobveg,
    gdf_distritos,
    how = 'intersection',
    keep_geom_type=True
)

Com esta função, caso um polígono de cobertura vegetal esteja dividido entre 2 ou mais distritos, eles serão divididos em diferente polígonos, recortados segundo os limites dos distritos. Mas, como os index (cd_cob_veg) se manterão, ainda poderemos saber quais poligonos correspondem a um poligono de cobertura vegetal anterior ao overlay.

In [9]:
overlay_gdf['area_recort'] = overlay_gdf['geometry'].area
overlay_gdf['perc_recort'] = overlay_gdf['area_recort']/overlay_gdf['area_cob_veg']

In [10]:
overlay_gdf.sample(2)

cd_cob_veg  cd_identi0  cd_categor  cd_subcate  cd_subcat0  \
40652      40183.0     40312.0        13.0         0.0         0.0   
203943    202150.0    202701.0        13.0         0.0         0.0   

        qt_altura_  area_cob_veg   CD_MUN     NM_MUN    CD_DIST  ...  CD_RGI  \
40652          0.0    259.387484  3550308  São Paulo  355030885  ...  350001   
203943         0.0     83.689085  3550308  São Paulo  355030837  ...  350001   

           NM_RGI CD_CONCURB    NM_CONCURB   AREA_KM2 total_pop total_dom  \
40652   São Paulo    3550308  São Paulo/SP   7.498376     92186     40616   
203943  São Paulo    3550308  São Paulo/SP  14.699172    210960     85467   

                                                 geometry  area_recort  \
40652   POLYGON ((341725.309 7394058.497, 341725.668 7...   259.387484   
203943  POLYGON ((351567.612 7396805.762, 351568.311 7...    83.689085   

       perc_recort  
40652          1.0  
203943         1.0  

[2 rows x 23 columns]

# Conferir consistência e compatibilidade

Vamos ver se há polígonos de cobertura vegetal que ficaram de fora após o overlay.

In [11]:
gdf_cobveg['cd_cob_veg'].unique().shape

(272117,)

In [12]:
overlay_gdf['cd_cob_veg'].unique().shape

(271652,)

Como há sim polígonos omitidos, vamos ver no mapa onde eles estão e se devem ser considerados ou não.

In [13]:
poligonos_omitidos = gdf_cobveg.loc[~gdf_cobveg['cd_cob_veg'].isin(overlay_gdf['cd_cob_veg'])]

In [14]:
poligonos_omitidos.shape

(465, 8)

In [15]:
m = gdf_distritos.explore(color='pink', fillOpacity=0.1)
poligonos_omitidos.explore(
    m=m,
    color='aquamarine'
)

As 465 áreas de cobertura vegetal que foram omitidas estão fora dos limites dos distritos e, portanto, do município. Por conta disso, optamos por não adicioná-los no cálculo, mantendo-os de fora do overlay.

# Salvar gdf

In [16]:
save_parquet_excel(
    overlay_gdf, 
    fname= 'overlay_cobertura_vegetal_distritos',
    data_path = data_path,
    data_subpath = os.path.join(
        'assets',
        'cobertura_vegetal'
    )
)